In [1]:
import os
os.environ['PYTHONHASHSEED']=str(0)

In [2]:
"""
Coin Game environment.
"""
import sys
import gym
import pylab
import random
import numpy as np
import tensorflow as tf
from keras.layers import Dense
from keras.models import Sequential
from keras.optimizers import Adam
from keras import backend as K

from gym.spaces import Discrete, Tuple
from gym.spaces import prng

np.random.seed(123)
random.seed(456)
prng.seed(456)

session_conf = tf.ConfigProto(intra_op_parallelism_threads=1, inter_op_parallelism_threads=1)


tf.set_random_seed(789)

sess = tf.Session(graph=tf.get_default_graph(), config=session_conf)
K.set_session(sess)


class CoinGameVec:
    """
    Vectorized Coin Game environment.
    Note: slightly deviates from the Gym API.
    """
    NUM_AGENTS = 2
    NUM_ACTIONS = 4
    MOVES = [
        np.array([0,  1]),
        np.array([0, -1]),
        np.array([1,  0]),
        np.array([-1, 0]), 
    ]

    def __init__(self, max_steps = 10, batch_size = 1, grid_size=3):
        self.max_steps = max_steps
        self.grid_size = grid_size
        self.batch_size = batch_size
        # The 4 channels stand for 2 players and 2 coin positions
        self.ob_space_shape = [4, grid_size, grid_size]

        self.step_count = None

    def reset(self):
        self.step_count = 0
        self.red_coin = prng.np_random.randint(2, size=self.batch_size)
        # Agent and coin positions
        self.red_pos  = prng.np_random.randint(
            self.grid_size, size=(self.batch_size, 2))
        self.blue_pos = prng.np_random.randint(
            self.grid_size, size=(self.batch_size, 2))
        self.coin_pos = np.zeros((self.batch_size, 2), dtype=np.int8)
        for i in range(self.batch_size):
            # Make sure coins don't overlap
            while self._same_pos(self.red_pos[i], self.blue_pos[i]):
                self.blue_pos[i] = prng.np_random.randint(self.grid_size, size=2)
            self._generate_coin(i)
        return self._generate_state()

    def _generate_coin(self, i):
        self.red_coin[i] = 1 - self.red_coin[i]
        # Make sure coin has a different position than the agents
        success = 0
        while success < 2:
            self.coin_pos[i] = prng.np_random.randint(self.grid_size, size=(2))
            success  = 1 - self._same_pos(self.red_pos[i],
                                          self.coin_pos[i])
            success += 1 - self._same_pos(self.blue_pos[i],
                                          self.coin_pos[i])

    def _same_pos(self, x, y):
        return (x == y).all()

    def _generate_state(self):
        state = np.zeros([self.batch_size] + self.ob_space_shape)
        for i in range(self.batch_size):
            state[i, 0, self.red_pos[i][0], self.red_pos[i][1]] = 1
            state[i, 1, self.blue_pos[i][0], self.blue_pos[i][1]] = 1
            if self.red_coin[i]:
                state[i, 2, self.coin_pos[i][0], self.coin_pos[i][1]] = 1
            else:
                state[i, 3, self.coin_pos[i][0], self.coin_pos[i][1]] = 1
        return state

    def step(self, action1, action2):
        for j in range(self.batch_size):
            ac0 = action1
            ac1 = action2
            assert ac0 in {0, 1, 2, 3} and ac1 in {0, 1, 2, 3}

            # Move players
            self.red_pos[j] = \
                (self.red_pos[j] + self.MOVES[ac0]) % self.grid_size
            self.blue_pos[j] = \
                (self.blue_pos[j] + self.MOVES[ac1]) % self.grid_size

        # Compute rewards
        reward_red, reward_blue = [], []
        for i in range(self.batch_size):
            generate = False
            if self.red_coin[i]:
                if self._same_pos(self.red_pos[i], self.coin_pos[i]):
                    generate = True
                    reward_red.append(0)
                    reward_blue.append(0)
                elif self._same_pos(self.blue_pos[i], self.coin_pos[i]):
                    generate = True
                    reward_red.append(0)
                    reward_blue.append(1)
                else:
                    reward_red.append(1)
                    reward_blue.append(0)

            else:
                if self._same_pos(self.blue_pos[i], self.coin_pos[i]):
                    generate = True
                    reward_red.append(0)
                    reward_blue.append(0)
                elif self._same_pos(self.red_pos[i], self.coin_pos[i]):
                    generate = True
                    reward_red.append(0)
                    reward_blue.append(1)
                else:
                    reward_red.append(1)
                    reward_blue.append(0)

            #if generate:
                #self._generate_coin(i)

        reward = [np.array(reward_red), np.array(reward_blue)]
        self.step_count += 1
        state = self._generate_state()

        return state, reward, generate

# A2C(Advantage Actor-Critic) agent for the Cartpole
class A2CAgent:
    def __init__(self, state_size, action_size):
        # if you want to see Cartpole learning, then change to True
        self.render = False
        self.load_model = False
        # get size of state and action
        self.state_size = state_size
        self.action_size = action_size
        self.value_size = 1
        self.action_table = [0,1,-4,4]
        self.lam = 0
        self.alpha = 0.2

        # These are hyper parameters for the Policy Gradient
        self.discount_factor = 1
        self.actor_lr = 0.005
        self.critic_lr = 0.005

        # create model for policy network
        self.actor = self.build_actor()        
        self.critic = self.build_critic()
        self.critic2 = self.build_critic2()

    # approximate policy and value using Neural Network
    # actor: state is input and probability of each action is output of model
    def build_actor(self):
        actor = Sequential()
        actor.add(Dense(48, input_dim=self.state_size, activation='relu',
                        kernel_initializer='he_uniform'))
        actor.add(Dense(self.action_size, activation='softmax',
                        kernel_initializer='he_uniform'))
        actor.summary()
        # See note regarding crossentropy in cartpole_reinforce.py
        actor.compile(loss='categorical_crossentropy',
                      optimizer=Adam(lr=self.actor_lr))
        return actor

    # critic: state is input and value of state is output of model
    def build_critic(self):
        critic = Sequential()
        critic.add(Dense(48, input_dim=self.state_size, activation='relu',
                         kernel_initializer='he_uniform'))
        critic.add(Dense(self.value_size, activation='linear',
                         kernel_initializer='he_uniform'))
        #critic.summary()
        critic.compile(loss="mse", optimizer=Adam(lr=self.critic_lr))
        return critic
    
    def build_critic2(self):
        critic = Sequential()
        critic.add(Dense(48, input_dim=self.state_size, activation='relu',
                         kernel_initializer='he_uniform'))
        critic.add(Dense(self.value_size, activation='linear',
                         kernel_initializer='he_uniform'))
        #critic.summary()
        critic.compile(loss="mse", optimizer=Adam(lr=self.critic_lr))
        return critic
        

    # using the output of policy network, pick action stochastically
    def get_action(self, state):
        policy = self.actor.predict(state, batch_size=1).flatten()
        return np.random.choice(self.action_size, 1, p=policy)[0]
    
    def get_maxaction(self,state):
        policy = self.actor.predict(state, batch_size=1).flatten()
        return np.argmax(policy)

    # update policy network every episode
    def train_model(self, state, action, reward1,reward2, next_state, done):
        target = np.zeros((1, self.value_size))
        advantages = np.zeros((1, self.action_size))
        target2 = np.zeros((1, self.value_size))     

        value = self.critic.predict(state)[0]
        value2 = self.critic2.predict(state)[0]
        next_value = self.critic.predict(next_state)[0]
        next_value2 = self.critic2.predict(next_state)[0]
        
        reward1 = reward1 + self.lam*(reward2 - self.alpha)

        if done:
            advantages[0][action] = -1*(reward1 - value)
            target[0][0] = reward1
            target2[0][0] = reward2
        else:
            advantages[0][action] = -1*(reward1 + self.discount_factor * (next_value) - value)
            target[0][0] = reward1 + self.discount_factor * next_value
            target2[0][0] = reward2 + self.discount_factor * next_value2
#             if np.where(next_state == 1.0)[1][0] == self.target_state:
#                 target2[0][0] = 0 + self.discount_factor * next_value2
#             else:
#                 target2[0][0] = np.where(next_state == 1.0)[1][0]/10 + self.discount_factor * next_value2            
            

        self.actor.fit(state, advantages, epochs=1, verbose=0)
        self.critic.fit(state, target, epochs=1, verbose=0)
        self.critic2.fit(state,target2,epochs = 1, verbose = 0)
        
        initial_state = np.zeros((1,state_size))
        initial_state[0][0] = 1
        self.lam = min(max(0,(self.lam + 0.001*(self.critic2.predict(state)[0] - self.alpha))), 10)
        #print(self.lam)
        
        
        

def intrepret_action(action):
    action1,action2 = np.divmod(action,4)
    return action1,action2
    
    

if __name__ == "__main__":
    # In case of CartPole-v1, maximum length of episode is 500
    #env = gym.make('CartPole-v1')
    # get size of state and action from environment
    state_size = 4*3*3 #env.observation_space.shape[0]
    action_size = 4*4 #env.action_space.n
    EPISODES = 10000

    # make A2C agent
    agent = A2CAgent(state_size, action_size)
    game = CoinGameVec()
    #agent = A2CAgent(state_size,action_size)
    
    
    
    
    
    average_penalty = 0
    total_penalty = 0
    store_penalty = np.zeros((1,EPISODES))
        
    average_lag = 0
    total_lag = 0
    store_lag = np.zeros((1,EPISODES))
    
    scores, episodes = [], []

    for i in range(1):
        done = False
        score = 0
        #state = env.reset()
        #state = np.reshape(state, [1, state_size])
        #rand_state = random.randint(0,15)
        #state = np.zeros((1,state_size))
        #state[0][rand_state] = 1
        #state = np.reshape(state, [1, state_size])
        
        for e in range(EPISODES):
        #state = env.reset()
            state = game.reset()
            state = np.reshape(state, [1, state_size])
            for time in range(10):
            # env.render()
                action = agent.get_action(state)
                action1,action2 = intrepret_action(action)
                
                next_state, reward, done = game.step(action1,action2)
                
            #reward = reward if not done else -10
                next_state = np.reshape(next_state, [1, state_size])
                agent.train_model(state, action,reward[0][0],reward[1][0],next_state, done)
                #agent2.train_model(state, action2, reward[0][0],reward[1][0],next_state, done)
                
                
                print(np.where(state == 1.0)[1][0],np.where(state == 1.0)[1][1] - 9,np.where(state == 1.0)[1][2],"--",action1, action2,"--",reward[0][0],reward[1][0],"--",np.where(next_state == 1.0)[1][0],np.where(next_state == 1.0)[1][1] - 9,np.where(next_state == 1.0)[1][2])
                
                #print(agent1.lam,agent2.lam)
                state = next_state
                
                average_penalty = average_penalty + reward[1][0]
                average_lag = average_lag + reward[0][0]
                
                if done:
                #print(state)
                    print("episode: {}/{}, score: {}"
                      .format(e, EPISODES, time))
                    print(agent.lam)
                    #print(agent2.lam)
                    break
                #if len(agent.memory) > batch_size:
                    #agent.replay(batch_size)
                    
            total_penalty = total_penalty + average_penalty        
            store_penalty[0][e] = total_penalty/(e+1) 
            print(store_penalty[0][e])
                
            total_lag = total_lag + average_lag
            store_lag[0][e] = total_lag/(e+1)
                
                #if np.mean(store_penalty[0][e-100:e]) < agent.alpha+0.1:
                        #sys.exit()
                #print(store_penalty[0][e])
            average_penalty = 0
            average_lag = 0
        
            print('*******************************')

/home/raghuram/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 48)                1776      
_________________________________________________________________
dense_2 (Dense)              (None, 16)                784       
Total params: 2,560
Trainable params: 2,560
Non-trainable params: 0
_________________________________________________________________
4 6 35 -- 2 3 -- 1 0 -- 7 3 35
7 3 35 -- 1 2 -- 1 0 -- 6 6 35
6 6 35 -- 3 3 -- 1 0 -- 3 3 35
3 3 35 -- 2 3 -- 1 0 -- 6 0 35
6 0 35 -- 2 0 -- 1 0 -- 0 1 35
0 1 35 -- 1 2 -- 1 0 -- 2 4 35
2 4 35 -- 1 2 -- 1 0 -- 1 7 35
1 7 35 -- 2 3 -- 1 0 -- 4 4 35
4 4 35 -- 1 2 -- 1 0 -- 3 7 35
3 7 35 -- 0 0 -- 0 0 -- 4 8 35
episode: 0/10000, score: 9
0
0.0
*******************************
3 4 19 -- 1 2 -- 1 0 -- 5 7 19
5 7 19 -- 2 3 -- 1 0 -- 8 4 19
8 4 19 -- 0 3 -- 0 1 -- 6 1 19
episode: 1/10000, score: 2
0
0.5
*******************************
1 5

0 7 23 -- 2 3 -- 1 0 -- 3 4 23
3 4 23 -- 3 1 -- 1 0 -- 0 3 23
0 3 23 -- 0 1 -- 0 1 -- 1 5 23
episode: 34/10000, score: 5
[0.00365213]
0.3142857142857143
*******************************
1 7 32 -- 3 2 -- 1 0 -- 7 1 32
7 1 32 -- 3 2 -- 1 0 -- 4 4 32
4 4 32 -- 3 3 -- 1 0 -- 1 1 32
1 1 32 -- 0 2 -- 1 0 -- 2 4 32
2 4 32 -- 0 1 -- 1 0 -- 0 3 32
0 3 32 -- 0 1 -- 0 0 -- 1 5 32
episode: 35/10000, score: 5
[0.00412696]
0.3055555555555556
*******************************
3 6 23 -- 1 2 -- 0 0 -- 5 0 23
episode: 36/10000, score: 0
[0.00401173]
0.2972972972972973
*******************************
6 7 29 -- 1 3 -- 1 0 -- 8 4 29
8 4 29 -- 2 1 -- 0 1 -- 2 3 29
episode: 37/10000, score: 1
[0.00421736]
0.3157894736842105
*******************************
8 1 23 -- 0 1 -- 1 0 -- 6 0 23
6 0 23 -- 0 3 -- 1 0 -- 7 6 23
7 6 23 -- 3 2 -- 1 0 -- 4 0 23
4 0 23 -- 2 1 -- 1 0 -- 7 2 23
7 2 23 -- 3 2 -- 0 1 -- 4 5 23
episode: 38/10000, score: 4
[0.00581259]
0.3333333333333333
*******************************
2 5 26 -- 0 0

5 7 18 -- 0 2 -- 1 0 -- 3 1 18
3 1 18 -- 1 1 -- 0 1 -- 5 0 18
episode: 70/10000, score: 2
[0.04147197]
0.323943661971831
*******************************
6 8 32 -- 3 0 -- 1 0 -- 3 6 32
3 6 32 -- 2 2 -- 1 0 -- 6 0 32
6 0 32 -- 2 2 -- 1 0 -- 0 3 32
0 3 32 -- 3 1 -- 0 0 -- 6 5 32
episode: 71/10000, score: 3
[0.04049671]
0.3194444444444444
*******************************
2 8 28 -- 0 1 -- 1 0 -- 0 7 28
0 7 28 -- 0 1 -- 0 1 -- 1 6 28
episode: 72/10000, score: 1
[0.04120057]
0.3287671232876712
*******************************
0 3 35 -- 0 1 -- 1 0 -- 1 5 35
1 5 35 -- 0 2 -- 0 0 -- 2 8 35
episode: 73/10000, score: 1
[0.04168079]
0.32432432432432434
*******************************
1 0 34 -- 0 1 -- 1 0 -- 2 2 34
2 2 34 -- 0 1 -- 1 0 -- 0 1 34
0 1 34 -- 1 0 -- 1 0 -- 2 2 34
2 2 34 -- 0 2 -- 1 0 -- 0 5 34
0 5 34 -- 1 2 -- 1 0 -- 2 8 34
2 8 34 -- 0 1 -- 0 0 -- 0 7 34
episode: 74/10000, score: 5
[0.0423051]
0.32
*******************************
8 4 34 -- 1 0 -- 0 1 -- 7 5 34
episode: 75/10000, score: 0


3 8 29 -- 1 0 -- 1 0 -- 5 6 29
5 6 29 -- 1 2 -- 1 0 -- 4 0 29
4 0 29 -- 1 0 -- 1 0 -- 3 1 29
3 1 29 -- 3 3 -- 1 0 -- 0 7 29
0 7 29 -- 0 2 -- 1 0 -- 1 1 29
1 1 29 -- 1 2 -- 1 0 -- 0 4 29
0 4 29 -- 1 2 -- 0 1 -- 2 7 29
episode: 110/10000, score: 6
[0.07941496]
0.35135135135135137
*******************************
0 1 29 -- 0 2 -- 1 0 -- 1 4 29
1 4 29 -- 3 3 -- 1 0 -- 7 1 29
7 1 29 -- 0 0 -- 0 0 -- 8 2 29
episode: 111/10000, score: 2
[0.08047626]
0.3482142857142857
*******************************
6 0 28 -- 0 2 -- 1 0 -- 7 3 28
7 3 28 -- 0 1 -- 1 0 -- 8 5 28
8 5 28 -- 0 1 -- 1 0 -- 6 4 28
6 4 28 -- 0 2 -- 1 0 -- 7 7 28
7 7 28 -- 2 2 -- 0 0 -- 1 1 28
episode: 112/10000, score: 4
[0.08298963]
0.34513274336283184
*******************************
1 6 25 -- 1 2 -- 1 0 -- 0 0 25
0 0 25 -- 0 0 -- 1 0 -- 1 1 25
1 1 25 -- 3 3 -- 0 0 -- 7 7 25
episode: 113/10000, score: 2
[0.08395412]
0.34210526315789475
*******************************
3 6 28 -- 1 3 -- 1 0 -- 5 3 28
5 3 28 -- 0 0 -- 1 0 -- 3 4 28
3 4 2

...

2 1 21 -- 1 0 -- 1 0 -- 1 2 21
1 2 21 -- 1 0 -- 1 0 -- 0 0 21
0 0 21 -- 1 0 -- 1 0 -- 2 1 21
2 1 21 -- 1 0 -- 1 0 -- 1 2 21
1 2 21 -- 1 0 -- 1 0 -- 0 0 21
0 0 21 -- 1 0 -- 1 0 -- 2 1 21
2 1 21 -- 1 0 -- 1 0 -- 1 2 21
0.24790345673961955
*******************************
7 5 29 -- 0 2 -- 1 0 -- 8 8 29
8 8 29 -- 3 2 -- 0 0 -- 5 2 29
episode: 9778/10000, score: 1
[1.6807142]
0.24787810614582267
*******************************
3 4 32 -- 0 0 -- 0 0 -- 4 5 32
episode: 9779/10000, score: 0
[1.6805779]
0.24785276073619633
*******************************
0 1 24 -- 0 2 -- 1 0 -- 1 4 24
1 4 24 -- 1 0 -- 1 0 -- 0 5 24
0 5 24 -- 3 3 -- 0 0 -- 6 2 24
episode: 9780/10000, score: 2
[1.6802098]
0.24782742050915038
*******************************
8 2 24 -- 1 0 -- 1 0 -- 7 0 24
7 0 24 -- 1 0 -- 0 0 -- 6 1 24
episode: 9781/10000, score: 1
[1.6800495]
0.24780208546309548
*******************************
7 4 18 -- 3 3 -- 1 0 -- 4 1 18
4 1 18 -- 3 3 -- 1 0 -- 1 7 18
1 7 18 -- 1 0 -- 0 0 -- 0 8 18
episode: 9782/

8 5 18 -- 3 3 -- 1 0 -- 5 2 18
5 2 18 -- 3 3 -- 1 0 -- 2 8 18
2 8 18 -- 1 3 -- 1 0 -- 1 5 18
1 5 18 -- 1 0 -- 0 0 -- 0 3 18
episode: 9833/10000, score: 3
[1.6688159]
0.24720357941834453
*******************************
6 8 29 -- 3 2 -- 0 0 -- 3 2 29
episode: 9834/10000, score: 0
[1.6686826]
0.24717844433146924
*******************************
5 4 25 -- 0 3 -- 1 0 -- 3 1 25
3 1 25 -- 1 0 -- 1 0 -- 5 2 25
5 2 25 -- 3 3 -- 1 0 -- 2 8 25
2 8 25 -- 1 0 -- 1 0 -- 1 6 25
1 6 25 -- 3 3 -- 0 0 -- 7 3 25
episode: 9835/10000, score: 4
[1.6684848]
0.24715331435542903
*******************************
3 1 27 -- 1 0 -- 1 0 -- 5 2 27
5 2 27 -- 1 0 -- 0 0 -- 4 0 27
episode: 9836/10000, score: 1
[1.6682273]
0.24712818948866525
*******************************
3 8 25 -- 1 3 -- 1 0 -- 5 5 25
5 5 25 -- 3 3 -- 1 0 -- 2 2 25
2 2 25 -- 3 3 -- 1 0 -- 8 8 25
8 8 25 -- 1 0 -- 0 0 -- 7 6 25
episode: 9837/10000, score: 3
[1.6677641]
0.24710306972961985
*******************************
5 6 22 -- 1 0 -- 0 0 -- 4 7 22
epi

0 1 21 -- 3 3 -- 1 0 -- 6 7 21
6 7 21 -- 3 3 -- 0 0 -- 3 4 21
episode: 9883/10000, score: 1
[1.6508039]
0.2461554026709834
*******************************
1 4 20 -- 0 2 -- 0 0 -- 2 7 20
episode: 9884/10000, score: 0
[1.6506107]
0.24613050075872533
*******************************
8 3 33 -- 2 2 -- 0 0 -- 2 6 33
episode: 9885/10000, score: 0
[1.6504288]
0.2461056038842808
*******************************
6 5 25 -- 0 2 -- 0 0 -- 7 8 25
episode: 9886/10000, score: 0
[1.650285]
0.24608071204612117
*******************************
5 1 18 -- 3 3 -- 1 0 -- 2 7 18
2 7 18 -- 1 0 -- 1 0 -- 1 8 18
1 8 18 -- 1 0 -- 0 0 -- 0 6 18
episode: 9887/10000, score: 2
[1.6496705]
0.24605582524271843
*******************************
1 6 21 -- 1 0 -- 1 0 -- 0 7 21
0 7 21 -- 3 3 -- 1 0 -- 6 4 21
6 4 21 -- 3 3 -- 0 0 -- 3 1 21
episode: 9888/10000, score: 2
[1.6492596]
0.24603094347254525
*******************************
0 1 29 -- 1 0 -- 0 0 -- 2 2 29
episode: 9889/10000, score: 0
[1.6490571]
0.24600606673407482
*****

5 4 33 -- 2 2 -- 1 0 -- 8 7 33
8 7 33 -- 1 0 -- 1 0 -- 7 8 33
7 8 33 -- 1 0 -- 0 0 -- 6 6 33
episode: 9941/10000, score: 2
[1.6303823]
0.2452222892778113
*******************************
2 8 28 -- 3 3 -- 1 0 -- 8 5 28
8 5 28 -- 1 0 -- 1 0 -- 7 3 28
7 3 28 -- 1 0 -- 1 0 -- 6 4 28
6 4 28 -- 3 3 -- 0 0 -- 3 1 28
episode: 9942/10000, score: 3
[1.6303735]
0.24519762647088403
*******************************
2 3 28 -- 1 0 -- 0 1 -- 1 4 28
episode: 9943/10000, score: 0
[1.6306508]
0.24527353177795655
*******************************
3 8 29 -- 3 2 -- 0 0 -- 0 2 29
episode: 9944/10000, score: 0
[1.63049]
0.24524886877828053
*******************************
0 5 22 -- 3 3 -- 1 0 -- 6 2 22
6 2 22 -- 1 3 -- 1 0 -- 8 8 22
8 8 22 -- 3 3 -- 1 0 -- 5 5 22
5 5 22 -- 1 0 -- 0 0 -- 4 3 22
episode: 9945/10000, score: 3
[1.6299016]
0.24522421073798512
*******************************
5 4 18 -- 3 3 -- 1 0 -- 2 1 18
2 1 18 -- 1 0 -- 1 0 -- 1 2 18
1 2 18 -- 1 0 -- 0 0 -- 0 0 18
episode: 9946/10000, score: 2
[1.6296

5 8 22 -- 1 3 -- 0 0 -- 4 5 22
episode: 9999/10000, score: 2
[1.6169311]
0.2445
*******************************


In [5]:

# A2C(Advantage Actor-Critic) agent for the Cartpole
class A2CAgent:
    def __init__(self, state_size, action_size):
        # if you want to see Cartpole learning, then change to True
        self.render = False
        self.load_model = False
        # get size of state and action
        self.state_size = state_size
        self.action_size = action_size
        self.value_size = 1
        self.action_table = [0,1,-4,4]
        self.lam = 0
        self.alpha = 0.2

        # These are hyper parameters for the Policy Gradient
        self.discount_factor = 1
        self.actor_lr = 0.005
        self.critic_lr = 0.005

        # create model for policy network
        self.actor = self.build_actor()        
        self.critic = self.build_critic()
        self.critic2 = self.build_critic2()

    # approximate policy and value using Neural Network
    # actor: state is input and probability of each action is output of model
    def build_actor(self):
        actor = Sequential()
        actor.add(Dense(48, input_dim=self.state_size, activation='relu',
                        kernel_initializer='he_uniform'))
        actor.add(Dense(self.action_size, activation='softmax',
                        kernel_initializer='he_uniform'))
        actor.summary()
        # See note regarding crossentropy in cartpole_reinforce.py
        actor.compile(loss='categorical_crossentropy',
                      optimizer=Adam(lr=self.actor_lr))
        return actor

    # critic: state is input and value of state is output of model
    def build_critic(self):
        critic = Sequential()
        critic.add(Dense(48, input_dim=self.state_size, activation='relu',
                         kernel_initializer='he_uniform'))
        critic.add(Dense(self.value_size, activation='linear',
                         kernel_initializer='he_uniform'))
        #critic.summary()
        critic.compile(loss="mse", optimizer=Adam(lr=self.critic_lr))
        return critic
    
    def build_critic2(self):
        critic = Sequential()
        critic.add(Dense(48, input_dim=self.state_size, activation='relu',
                         kernel_initializer='he_uniform'))
        critic.add(Dense(self.value_size, activation='linear',
                         kernel_initializer='he_uniform'))
        #critic.summary()
        critic.compile(loss="mse", optimizer=Adam(lr=self.critic_lr))
        return critic
        

    # using the output of policy network, pick action stochastically
    def get_action(self, state):
        policy = self.actor.predict(state, batch_size=1).flatten()
        return np.random.choice(self.action_size, 1, p=policy)[0]
    
    def get_maxaction(self,state):
        policy = self.actor.predict(state, batch_size=1).flatten()
        return np.argmax(policy)

    # update policy network every episode
    def train_model(self, state, action, reward1,reward2, next_state, done):
        target = np.zeros((1, self.value_size))
        advantages = np.zeros((1, self.action_size))
        target2 = np.zeros((1, self.value_size))     

        value = self.critic.predict(state)[0]
        value2 = self.critic2.predict(state)[0]
        next_value = self.critic.predict(next_state)[0]
        next_value2 = self.critic2.predict(next_state)[0]
        
        reward1 = reward1 + self.lam*(reward2 - self.alpha)

        if done:
            advantages[0][action] = -1*(reward1 - value)
            target[0][0] = reward1
            target2[0][0] = reward2
        else:
            advantages[0][action] = -1*(reward1 + self.discount_factor * (next_value) - value)
            target[0][0] = reward1 + self.discount_factor * next_value
            target2[0][0] = reward2 + self.discount_factor * next_value2
#             if np.where(next_state == 1.0)[1][0] == self.target_state:
#                 target2[0][0] = 0 + self.discount_factor * next_value2
#             else:
#                 target2[0][0] = np.where(next_state == 1.0)[1][0]/10 + self.discount_factor * next_value2            
            

        self.actor.fit(state, advantages, epochs=1, verbose=0)
        self.critic.fit(state, target, epochs=1, verbose=0)
        self.critic2.fit(state,target2,epochs = 1, verbose = 0)
        
        initial_state = np.zeros((1,state_size))
        initial_state[0][0] = 1
        self.lam = min(max(0,(self.lam + 0.001*(self.critic2.predict(state)[0] - self.alpha))), 10)
        #print(self.lam)
        
        
        

def intrepret_action(action):
    action1,action2 = np.divmod(action,4)
    return action1,action2
    
    

if __name__ == "__main__":
    # In case of CartPole-v1, maximum length of episode is 500
    #env = gym.make('CartPole-v1')
    # get size of state and action from environment
    state_size = 4*3*3 #env.observation_space.shape[0]
    action_size = 4*4 #env.action_space.n
    EPISODES = 10000

    # make A2C agent
    agent = A2CAgent(state_size, action_size)
    game = CoinGameVec()
    #agent = A2CAgent(state_size,action_size)
    
    
    
    
    
    average_penalty = 0
    total_penalty = 0
    store_penalty = np.zeros((1,EPISODES))
        
    average_lag = 0
    total_lag = 0
    store_lag = np.zeros((1,EPISODES))
    
    scores, episodes = [], []

    for i in range(1):
        done = False
        score = 0
        #state = env.reset()
        #state = np.reshape(state, [1, state_size])
        #rand_state = random.randint(0,15)
        #state = np.zeros((1,state_size))
        #state[0][rand_state] = 1
        #state = np.reshape(state, [1, state_size])
        
        for e in range(EPISODES):
        #state = env.reset()
            state = game.reset()
            state = np.reshape(state, [1, state_size])
            for time in range(10):
            # env.render()
                action = agent.get_action(state)
                action1,action2 = intrepret_action(action)
                
                next_state, reward, done = game.step(action1,action2)
                
            #reward = reward if not done else -10
                next_state = np.reshape(next_state, [1, state_size])
                agent.train_model(state, action,reward[0][0],reward[1][0],next_state, done)
                #agent2.train_model(state, action2, reward[0][0],reward[1][0],next_state, done)
                
                
                print(np.where(state == 1.0)[1][0],np.where(state == 1.0)[1][1] - 9,np.where(state == 1.0)[1][2],"--",action1, action2,"--",reward[0][0],reward[1][0],"--",np.where(next_state == 1.0)[1][0],np.where(next_state == 1.0)[1][1] - 9,np.where(next_state == 1.0)[1][2])
                
                #print(agent1.lam,agent2.lam)
                state = next_state
                
                average_penalty = average_penalty + reward[1][0]
                average_lag = average_lag + reward[0][0]
                
                if done:
                #print(state)
                    print("episode: {}/{}, score: {}"
                      .format(e, EPISODES, time))
                    print(agent.lam)
                    #print(agent2.lam)
                    break
                #if len(agent.memory) > batch_size:
                    #agent.replay(batch_size)
                    
            total_penalty = total_penalty + average_penalty        
            store_penalty[0][e] = total_penalty/(e+1) 
            print(store_penalty[0][e])
                
            total_lag = total_lag + average_lag
            store_lag[0][e] = total_lag/(e+1)
                
                #if np.mean(store_penalty[0][e-100:e]) < agent.alpha+0.1:
                        #sys.exit()
                #print(store_penalty[0][e])
            average_penalty = 0
            average_lag = 0
        
            print('*******************************')

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_7 (Dense)              (None, 48)                1776      
_________________________________________________________________
dense_8 (Dense)              (None, 16)                784       
Total params: 2,560
Trainable params: 2,560
Non-trainable params: 0
_________________________________________________________________
4 2 35 -- 3 0 -- 1 0 -- 1 0 35
1 0 35 -- 1 0 -- 1 0 -- 0 1 35
0 1 35 -- 0 3 -- 1 0 -- 1 7 35
1 7 35 -- 2 0 -- 0 0 -- 4 8 35
episode: 0/10000, score: 3
0
0.0
*******************************
7 8 28 -- 3 0 -- 1 0 -- 4 6 28
4 6 28 -- 1 2 -- 1 0 -- 3 0 28
3 0 28 -- 3 3 -- 1 0 -- 0 6 28
0 6 28 -- 2 2 -- 1 0 -- 3 0 28
3 0 28 -- 1 3 -- 1 0 -- 5 6 28
5 6 28 -- 1 2 -- 1 0 -- 4 0 28
4 0 28 -- 1 1 -- 1 0 -- 3 2 28
3 2 28 -- 2 2 -- 1 0 -- 6 5 28
6 5 28 -- 1 3 -- 1 0 -- 8 2 28
8 2 28 -- 0 1 -- 0 0 -- 6 1 28
episode: 1/10000, score: 9
0
0.0
****

7 8 24 -- 0 3 -- 1 0 -- 8 5 24
8 5 24 -- 0 2 -- 0 0 -- 6 8 24
episode: 38/10000, score: 1
[0.01368792]
0.3076923076923077
*******************************
6 8 19 -- 2 3 -- 1 0 -- 0 5 19
0 5 19 -- 0 1 -- 0 0 -- 1 4 19
episode: 39/10000, score: 1
[0.01393787]
0.3
*******************************
1 7 29 -- 2 0 -- 1 0 -- 4 8 29
4 8 29 -- 3 2 -- 0 0 -- 1 2 29
episode: 40/10000, score: 1
[0.01411911]
0.2926829268292683
*******************************
4 6 19 -- 2 1 -- 1 0 -- 7 8 19
7 8 19 -- 1 0 -- 1 0 -- 6 6 19
6 6 19 -- 1 1 -- 1 0 -- 8 8 19
8 8 19 -- 2 2 -- 1 0 -- 2 2 19
2 2 19 -- 1 3 -- 0 0 -- 1 8 19
episode: 41/10000, score: 4
[0.01489323]
0.2857142857142857
*******************************
7 1 33 -- 0 0 -- 1 0 -- 8 2 33
8 2 33 -- 2 0 -- 1 0 -- 2 0 33
2 0 33 -- 3 2 -- 1 0 -- 8 3 33
8 3 33 -- 0 3 -- 0 1 -- 6 0 33
episode: 42/10000, score: 3
[0.01616533]
0.3023255813953488
*******************************
5 0 24 -- 3 2 -- 1 0 -- 2 3 24
2 3 24 -- 2 2 -- 0 1 -- 5 6 24
episode: 43/10000, score: 1


8 2 32 -- 0 1 -- 1 0 -- 6 1 32
6 1 32 -- 3 2 -- 1 0 -- 3 4 32
3 4 32 -- 0 0 -- 0 0 -- 4 5 32
episode: 83/10000, score: 6
[0.0368242]
0.34523809523809523
*******************************
0 8 28 -- 3 2 -- 1 0 -- 6 2 28
6 2 28 -- 3 2 -- 1 0 -- 3 5 28
3 5 28 -- 3 1 -- 1 0 -- 0 4 28
0 4 28 -- 0 0 -- 0 1 -- 1 5 28
episode: 84/10000, score: 3
[0.03724594]
0.35294117647058826
*******************************
0 1 22 -- 2 0 -- 1 0 -- 3 2 22
3 2 22 -- 0 0 -- 0 0 -- 4 0 22
episode: 85/10000, score: 1
[0.03760816]
0.3488372093023256
*******************************
7 6 30 -- 2 2 -- 1 0 -- 1 0 30
1 0 30 -- 0 0 -- 1 0 -- 2 1 30
2 1 30 -- 0 0 -- 1 0 -- 0 2 30
0 2 30 -- 0 0 -- 1 0 -- 1 0 30
1 0 30 -- 3 2 -- 0 0 -- 7 3 30
episode: 86/10000, score: 4
[0.03985574]
0.3448275862068966
*******************************
3 5 19 -- 1 0 -- 1 0 -- 5 3 19
5 3 19 -- 1 2 -- 1 0 -- 4 6 19
4 6 19 -- 2 0 -- 1 0 -- 7 7 19
7 7 19 -- 0 0 -- 1 0 -- 8 8 19
8 8 19 -- 0 3 -- 1 0 -- 6 5 19
6 5 19 -- 2 1 -- 1 0 -- 0 4 19
0 4 19 -- 0

1 3 29 -- 0 0 -- 0 1 -- 2 4 29
episode: 122/10000, score: 2
[0.07376297]
0.37398373983739835
*******************************
3 1 18 -- 0 0 -- 1 0 -- 4 2 18
4 2 18 -- 3 0 -- 0 1 -- 1 0 18
episode: 123/10000, score: 1
[0.07410955]
0.3790322580645161
*******************************
2 3 26 -- 0 0 -- 1 0 -- 0 4 26
0 4 26 -- 2 0 -- 1 0 -- 3 5 26
3 5 26 -- 3 2 -- 0 1 -- 0 8 26
episode: 124/10000, score: 2
[0.07515661]
0.384
*******************************
0 8 21 -- 0 3 -- 1 0 -- 1 5 21
1 5 21 -- 0 0 -- 0 1 -- 2 3 21
episode: 125/10000, score: 1
[0.07552163]
0.3888888888888889
*******************************
3 1 35 -- 0 0 -- 1 0 -- 4 2 35
4 2 35 -- 3 2 -- 1 0 -- 1 5 35
1 5 35 -- 3 2 -- 0 0 -- 7 8 35
episode: 126/10000, score: 2
[0.07634141]
0.3858267716535433
*******************************
3 6 29 -- 1 2 -- 1 0 -- 5 0 29
5 0 29 -- 0 3 -- 1 0 -- 3 6 29
3 6 29 -- 2 0 -- 1 0 -- 6 7 29
6 7 29 -- 3 1 -- 1 0 -- 3 6 29
3 6 29 -- 2 2 -- 1 0 -- 6 0 29
6 0 29 -- 0 3 -- 1 0 -- 7 6 29
7 6 29 -- 3 2 -- 1 0

4 8 18 -- 0 0 -- 1 0 -- 5 6 18
5 6 18 -- 0 0 -- 1 0 -- 3 7 18
3 7 18 -- 3 0 -- 0 0 -- 0 8 18
episode: 163/10000, score: 2
[0.12221214]
0.3902439024390244
*******************************
4 5 25 -- 0 0 -- 1 0 -- 5 3 25
5 3 25 -- 0 0 -- 1 0 -- 3 4 25
3 4 25 -- 0 0 -- 1 0 -- 4 5 25
4 5 25 -- 3 2 -- 1 0 -- 1 8 25
1 8 25 -- 3 2 -- 0 0 -- 7 2 25
episode: 164/10000, score: 4
[0.12324174]
0.3878787878787879
*******************************
4 2 19 -- 0 0 -- 1 0 -- 5 0 19
5 0 19 -- 3 2 -- 1 0 -- 2 3 19
2 3 19 -- 0 0 -- 1 0 -- 0 4 19
0 4 19 -- 0 0 -- 0 0 -- 1 5 19
episode: 165/10000, score: 3
[0.12390215]
0.3855421686746988
*******************************
4 7 24 -- 3 2 -- 1 0 -- 1 1 24
1 1 24 -- 3 2 -- 1 0 -- 7 4 24
7 4 24 -- 0 0 -- 1 0 -- 8 5 24
8 5 24 -- 3 2 -- 1 0 -- 5 8 24
5 8 24 -- 2 0 -- 0 1 -- 8 6 24
episode: 166/10000, score: 4
[0.12466323]
0.38922155688622756
*******************************
0 6 21 -- 0 0 -- 1 0 -- 1 7 21
1 7 21 -- 0 0 -- 1 0 -- 2 8 21
2 8 21 -- 0 2 -- 1 0 -- 0 2 21
0 2 21 

...

6 5 35 -- 3 2 -- 0 0 -- 3 8 35
episode: 9728/10000, score: 1
[2.3750234]
0.2980779113989105
*******************************
8 2 23 -- 3 2 -- 0 0 -- 5 5 23
episode: 9729/10000, score: 0
[2.3752067]
0.29804727646454265
*******************************
2 6 28 -- 2 0 -- 1 0 -- 5 7 28
5 7 28 -- 3 2 -- 0 0 -- 2 1 28
episode: 9730/10000, score: 1
[2.3748536]
0.29801664782653375
*******************************
3 8 22 -- 0 3 -- 0 0 -- 4 5 22
episode: 9731/10000, score: 0
[2.3746612]
0.2979860254829429
*******************************
3 4 29 -- 3 2 -- 1 0 -- 0 7 29
0 7 29 -- 3 2 -- 1 0 -- 6 1 29
6 1 29 -- 0 0 -- 0 0 -- 7 2 29
episode: 9732/10000, score: 2
[2.3742874]
0.29795540943182985
*******************************
5 6 18 -- 3 0 -- 1 0 -- 2 7 18
2 7 18 -- 0 0 -- 0 0 -- 0 8 18
episode: 9733/10000, score: 1
[2.3738866]
0.2979247996712554
*******************************
5 0 35 -- 3 2 -- 1 0 -- 2 3 35
2 3 35 -- 3 0 -- 0 1 -- 8 4 35
episode: 9734/10000, score: 1
[2.3754368]
0.29799691833590136
*****

6 1 18 -- 2 0 -- 0 0 -- 0 2 18
episode: 9788/10000, score: 0
[2.3582947]
0.2967616712636633
*******************************
2 3 33 -- 3 2 -- 0 0 -- 8 6 33
episode: 9789/10000, score: 0
[2.3581822]
0.2967313585291113
*******************************
5 1 22 -- 0 3 -- 1 0 -- 3 7 22
3 7 22 -- 0 3 -- 0 0 -- 4 4 22
episode: 9790/10000, score: 1
[2.3579245]
0.29670105198651825
*******************************
6 0 22 -- 3 2 -- 1 0 -- 3 3 22
3 3 22 -- 0 3 -- 0 0 -- 4 0 22
episode: 9791/10000, score: 1
[2.3574576]
0.29667075163398693
*******************************
4 5 33 -- 3 0 -- 1 0 -- 1 3 33
1 3 33 -- 3 2 -- 0 0 -- 7 6 33
episode: 9792/10000, score: 1
[2.357088]
0.29664045746962114
*******************************
7 6 27 -- 0 0 -- 1 0 -- 8 7 27
8 7 27 -- 0 0 -- 1 0 -- 6 8 27
6 8 27 -- 2 2 -- 0 1 -- 0 2 27
episode: 9793/10000, score: 2
[2.3569515]
0.29671227282009394
*******************************
6 4 35 -- 3 2 -- 1 0 -- 3 7 35
3 7 35 -- 3 0 -- 0 0 -- 0 8 35
episode: 9794/10000, score: 1
[2.356

7 3 31 -- 2 0 -- 0 0 -- 1 4 31
episode: 9842/10000, score: 0
[2.3370962]
0.2954383826069288
*******************************
8 7 23 -- 3 3 -- 0 0 -- 5 4 23
episode: 9843/10000, score: 0
[2.3368986]
0.2954083705810646
*******************************
2 3 34 -- 0 0 -- 1 0 -- 0 4 34
0 4 34 -- 3 2 -- 0 0 -- 6 7 34
episode: 9844/10000, score: 1
[2.3364358]
0.29537836465210765
*******************************
1 4 27 -- 0 0 -- 1 0 -- 2 5 27
2 5 27 -- 0 0 -- 0 1 -- 0 3 27
episode: 9845/10000, score: 1
[2.336975]
0.29544992890513916
*******************************
5 2 26 -- 3 2 -- 1 0 -- 2 5 26
2 5 26 -- 3 0 -- 0 0 -- 8 3 26
episode: 9846/10000, score: 1
[2.3364124]
0.2954199248502082
*******************************
1 4 35 -- 3 2 -- 1 0 -- 7 7 35
7 7 35 -- 3 0 -- 0 0 -- 4 8 35
episode: 9847/10000, score: 1
[2.3359368]
0.29538992688870835
*******************************
3 5 35 -- 3 2 -- 0 0 -- 0 8 35
episode: 9848/10000, score: 0
[2.3357081]
0.29535993501878366
*******************************
0 2 3

5 4 29 -- 3 2 -- 0 1 -- 2 7 29
episode: 9897/10000, score: 0
[2.3295712]
0.2948070317235805
*******************************
0 7 19 -- 0 0 -- 0 0 -- 1 8 19
episode: 9898/10000, score: 0
[2.3293831]
0.2947772502272957
*******************************
4 1 18 -- 0 0 -- 1 0 -- 5 2 18
5 2 18 -- 3 2 -- 1 0 -- 2 5 18
2 5 18 -- 0 0 -- 0 0 -- 0 3 18
episode: 9899/10000, score: 2
[2.3289344]
0.29474747474747476
*******************************
8 2 25 -- 0 0 -- 1 0 -- 6 0 25
6 0 25 -- 0 3 -- 0 0 -- 7 6 25
episode: 9900/10000, score: 1
[2.3285842]
0.29471770528229474
*******************************
2 3 19 -- 0 0 -- 1 0 -- 0 4 19
0 4 19 -- 0 0 -- 0 0 -- 1 5 19
episode: 9901/10000, score: 1
[2.3281493]
0.29468794182993335
*******************************
5 0 21 -- 0 3 -- 0 0 -- 3 6 21
episode: 9902/10000, score: 0
[2.3282456]
0.2946581843885691
*******************************
2 3 33 -- 3 2 -- 0 0 -- 8 6 33
episode: 9903/10000, score: 0
[2.3280342]
0.29462843295638125
*******************************
5 7 

5 1 27 -- 0 0 -- 1 0 -- 3 2 27
3 2 27 -- 0 0 -- 0 0 -- 4 0 27
episode: 9954/10000, score: 2
[2.3119037]
0.29352084379708687
*******************************
3 6 23 -- 0 3 -- 1 0 -- 4 3 23
4 3 23 -- 0 3 -- 0 0 -- 5 0 23
episode: 9955/10000, score: 1
[2.3115065]
0.2934913619927682
*******************************
1 7 21 -- 0 3 -- 1 0 -- 2 4 21
2 4 21 -- 0 3 -- 1 0 -- 0 1 21
0 1 21 -- 2 0 -- 0 0 -- 3 2 21
episode: 9956/10000, score: 2
[2.3109128]
0.2934618861102742
*******************************
5 7 33 -- 3 0 -- 1 0 -- 2 8 33
2 8 33 -- 3 0 -- 0 0 -- 8 6 33
episode: 9957/10000, score: 1
[2.3105416]
0.29343241614782084
*******************************
6 5 22 -- 3 2 -- 1 0 -- 3 8 22
3 8 22 -- 0 3 -- 0 0 -- 4 5 22
episode: 9958/10000, score: 1
[2.3101056]
0.2934029521036249
*******************************
6 7 31 -- 0 3 -- 0 0 -- 7 4 31
episode: 9959/10000, score: 0
[2.3099463]
0.2933734939759036
*******************************
6 3 26 -- 0 0 -- 1 0 -- 7 4 26
7 4 26 -- 0 0 -- 0 0 -- 8 5 26
episod

In [5]:
np.random.seed(99)
random.seed(999)
prng.seed(999)

count = 0
total = 10000
for i in range(total):
    state = game.reset()
    state = np.reshape(state, [1, state_size])
    for time in range(10):
                # env.render()
        action= agent.get_maxaction(state)
        action1,action2 = intrepret_action(action)
        #action2 = agent2.get_action(state)

        next_state, reward, done = game.step(action1,action2)

                #reward = reward if not done else -10
        next_state = np.reshape(next_state, [1, state_size])  
        #print(np.where(state == 1.0)[1][0],np.where(state == 1.0)[1][1] - 9,np.where(state == 1.0)[1][2],"--",action1, action2,"--",reward[0][0],reward[1][0],"--",np.where(next_state == 1.0)[1][0],np.where(next_state == 1.0)[1][1] - 9,np.where(next_state == 1.0)[1][2])

                    #print(agent1.lam,agent2.lam)
        state = next_state
        #print(agent.critic2.predict(state)[0])
        if done:
                    #print(state)
            #print("episode: {}/{}, score: {}"
                    #.format(e, EPISODES, time))
            #print(agent.lam)
            #print(agent2.lam)
            if reward[1][0] == 1:
                count = count+1
            
            break
                    #if len(agent.memory) > batch_size:
                        #agent.replay(batch_size)

                   #print('*******************************')
print(count/total)

0.1069


In [4]:
np.savetxt('CGJAL_penalty',store_penalty)
np.savetxt('CGJAL_Lag',store_lag)